In [ ]:
import dash_bootstrap_components as dbc
from dash import Dash, html, dash_table, dcc, callback, Output, Input, State
import pandas as pd
import plotly.express as px
import os
import plotly.graph_objects as go
import requests
from bs4 import BeautifulSoup
from io import StringIO
import re

In [ ]:
# Hardcode path to files and create list of all missions
folder_path = "https://www3.mbari.org/lobo/Data/GliderVizData/"

response = requests.get(folder_path)
soup = BeautifulSoup(response.text, 'html.parser')

# Get clean filenames without path or extension
# Get just the filename with extension (no path)
files = [
    os.path.basename(a['href'])
    for a in soup.find_all('a', href=True)
    if 'RT.txt' in a['href']
]

# Load and clean data
def load_latest_data(folder_path, selected_file=None):
    """Loads the latest RT.txt file, cleans it, and returns a DataFrame."""
    filename = selected_file if selected_file else files[-1]
    file_url = folder_path + filename
    file_response = requests.get(file_url)
    file_content = StringIO(file_response.text)
    df = pd.read_csv(file_content, delimiter="\t", skiprows=6)

    # Clean data
    df.columns = df.columns.str.replace('Â', '') # Issue when importing from html
    df.replace(-1e10, pd.NA, inplace=True)
    df.replace(-999, pd.NA, inplace=True)
    df['Date'] = pd.to_datetime(df['mon/day/yr'], format='%m/%d/%Y')
    df['Datetime'] = pd.to_datetime(df['mon/day/yr'] + ' ' + df['hh:mm'], format='%m/%d/%Y %H:%M')
    # Only calculate pHin_Canb_Delta if 'PHIN_CANYONB[Total]' exists
    if 'PHIN_CANYONB[Total]' in df.columns:
        df['pHin_Canb_Delta'] = df['pHinsitu[Total]'] - df['PHIN_CANYONB[Total]']
    else:
        df['pHin_Canb_Delta'] = pd.NA  # Optional: Add the column as all-NA if needed     
    return df

df = load_latest_data(folder_path)

In [ ]:
files[-1]

In [ ]:
folder_path = r"\\atlas.shore.mbari.org\ProjectLibrary\901805_Coastal_Biogeochemical_Sensing\Wetlab_Sensor_Calibration\NanoFet"

files = [f for f in os.listdir(folder_path) if '.csv']

selected_file = files[-1]
filename = os.path.join(folder_path, folder_path, selected_file if selected_file else files[-1])

df = pd.read_csv(filename, delimiter=",", skiprows=4)

df['DateTime'] = pd.to_datetime(df['DateTime'], format='%Y-%m-%d %H:%M')    


df


In [ ]:
# Calculate pairwise differences
differences = []
for i in range(len(df['Vrse'])):
    for j in range(i+1, len(df['Vrse'])):
        differences.append(df['NanoFet'][j] - df['NanoFet'][i])

# Calculate mean of all pairwise differences
mean_difference = np.mean(differences, axis=0)

In [25]:
import dash_bootstrap_components as dbc
from dash import Dash, html, dcc, callback, Output, Input
from dash.exceptions import PreventUpdate
import pandas as pd
import numpy as np
import plotly.express as px
import os
import plotly.graph_objects as go

# Hardcode path to files and create list of all missions
folder_path = r"\\atlas.shore.mbari.org\ProjectLibrary\901805_Coastal_Biogeochemical_Sensing\WireWalker\MBARI\data"
file_name = "WW_Upcast_1Hz.txt"
file_path = os.path.join(folder_path, file_name)
# Load and clean data
def load_latest_data(file_path, downsample_factor):
    """Loads the latest RT.txt file, cleans it, and returns a DataFrame."""
    df = pd.read_csv(file_path, delimiter=",",skiprows=lambda i: i != 0 and i % downsample_factor != 0)
    
    # Clean data
        # Add some QC data

    # Make datetime
    df['Date'] = pd.to_datetime(df['mm/dd/yyyy'], format='%m/%d/%Y')
    df['Datetime'] = pd.to_datetime(df['mm/dd/yyyy'] + ' ' + df['HH:MM:SS'], format='%m/%d/%Y %H:%M:%S')
    
    return df

def filter_dataframe(df, filter_method, station_range, start_date, end_date, profile_number, depth_range):
    # Filter by station range, date range, or profile number
    if filter_method == 'station':
        df = df[(df['Station'] >= station_range[0]) & (df['Station'] <= station_range[1])]
    elif filter_method == 'date':
        df = df[(df['Date'] >= start_date) & (df['Date'] <= end_date)]
    elif filter_method == 'profile' and profile_number is not None:
        df = df[df['Station'] == profile_number]
    
    # Filter by depth range
    df = df[(df['Depth'] >= depth_range[0]) & (df['Depth'] <= depth_range[1])]
    
    return df

downsample_init = 8
downsample_factor = downsample_init # initially set to 2 for first load, 10 for testing
df = load_latest_data(file_path,downsample_factor)

In [28]:
# df = px.data.tips()
# df2 = df[(df["Station"] >= 2000) & (df["Station"] <= 4000)]
df2 = df[df["Station"] >= 20]

In [ ]:
from scipy.interpolate import griddata
from scipy.ndimage import gaussian_filter

df2['Time_numeric'] = pd.to_datetime(df2['Datetime']).astype(np.int64) / 1e9  # seconds

# Grid step sizes
depth_step = 5      # 1 meter
time_step = 300       # 8 seconds

# Define depth grid
depth_grid = np.arange(0, 100+depth_step, depth_step)

# Define time grid (in seconds since epoch)
time_grid = np.arange(df2['Time_numeric'].min(), df2['Time_numeric'].max(), time_step)

# Create meshgrid
depth_mesh, time_mesh = np.meshgrid(depth_grid, time_grid)

points = np.column_stack((df2['Time_numeric'], df2['Depth']))
values = df2['pH']

# Interpolate to regular grid
ph_grid = griddata(points, values, (time_mesh, depth_mesh), method='linear')

# Convert numeric time back to datetime
time_grid_dt = pd.to_datetime(time_grid, unit='s')

fig = px.imshow(
    ph_grid.T,  # transpose to get [depth x time]
    x=time_grid_dt,
    y=depth_grid,
    # aspect='auto',
    origin='lower',
    color_continuous_scale='Viridis',
    labels={'x': 'Time', 'y': 'Depth', 'color': 'pH'},
    title='Interpolated pH over Time and Depth',
    
    # range_color=[7.4, 8.1],
)

fig.update_yaxes(autorange='reversed')  # Optional: make depth increase downward
fig.show()


C:\Users\bwerb\AppData\Local\Temp\ipykernel_29732\360784787.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

